# 핵심 키워드 추출 (Keyword Extraction)

In [ ]:
# Mecab 설치
!apt-get update
!apt-get install g++ openjdk-8-jdk
!pip3 install konlpy JPype1-py3
!bash <(curl -s https://raw.githubusercontent.com/konlpy/konlpy/master/scripts/mecab.sh)

In [ ]:
# mecab-python의 버전 오류로 인해 아래 패키지를 설치하면 코랩에서 Mecab을 사용가능
!pip install mecab-python3

In [ ]:
!sudo apt-get install -y fonts-nanum
!sudo fc-cache -fv
!rm ~/.cache/matplotlib -rf

# 패키지 업그레이드로 인한 에러 처리를 위해 라이브러리 버전 Downgrade
!pip install 'networkx<2.7'

# 런타임 재시작 !

In [4]:
import matplotlib.pyplot as plt
plt.rc('font', family='NanumBarunGothic')
plt.rcParams['axes.unicode_minus'] = False

import warnings
warnings.filterwarnings('ignore')

# 1.1 TF-IDF 활용 핵심키워드 추출

## 실습 1. sklearn 활용

In [5]:
import requests
from bs4 import BeautifulSoup

def get_news_by_url(url):
    res = requests.get(url, headers = {
        'User-Agent': 'Mozilla/5.0'
    })
    bs = BeautifulSoup(res.content, 'html.parser')

    title = bs.select_one('#title_area').text #제목
    content = bs.select_one('#contents').get_text().replace('\n', " ") #본문
    content = content.replace("// flash 오류를 우회하기 위한 함수 추가 function _flash_removeCallback() {}", "")
    return  content.strip()

docs = []
docs.append( get_news_by_url('https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=105&oid=018&aid=0004430108') )
docs.append( get_news_by_url('https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=101&oid=001&aid=0011614790') )
docs.append( get_news_by_url('https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=102&oid=014&aid=0004424362') )
docs.append( get_news_by_url('https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=101&oid=119&aid=0002402191') )
docs.append( get_news_by_url('https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=101&oid=030&aid=0002882728') )
len(docs)

5

### 1) 전처리

In [6]:
from konlpy.tag import Mecab
mecab = Mecab() 

preprocessed_docs = []
for doc in docs :
    # 명사와 동사만으로 문서 전처리
    preprocessed_docs.append(' '.join([token[0] for token in mecab.pos(doc) if token[1][0] in ['N', 'V']]))
preprocessed_docs[0][:100]

'과기 정통부 일 유영민 장관 등 참석 기념행사 년 억 원 투입 여종 데이터 구축 민간 클라우드 통한 외부 연계 체계 개방 강화 데일리 이재운 기자 국가 차원 빅 데이터 활용 시대 '

### 2) TF-IDF 계산

In [7]:
from sklearn.feature_extraction.text import CountVectorizer

count_vectorizer = CountVectorizer(max_df=0.85, max_features=10000)
word_count_vector = count_vectorizer.fit_transform(preprocessed_docs)
list(count_vectorizer.vocabulary_.keys())[:10]

['과기', '정통부', '유영민', '장관', '참석', '기념행사', '투입', '여종', '구축', '민간']

In [8]:
from sklearn.feature_extraction.text import TfidfTransformer

tfidf_transformer = TfidfTransformer(smooth_idf=True, use_idf=True)
tfidf_transformer.fit(word_count_vector)

TfidfTransformer()

### 3) 핵심키워드 추출

In [9]:
def sort_keywords(keywords):
    return sorted(zip(keywords.col, keywords.data), key=lambda x: (x[1], x[0]), reverse=True)

def extract_keywords(feature_names, sorted_keywords, n=5):
    return [(feature_names[idx], score) for idx, score in sorted_keywords[:n]]

In [10]:
doc = preprocessed_docs[0] # 핵심키워드 추출할 문서 조회

feature_names = count_vectorizer.get_feature_names_out() # TF-IDF 단어 목록
tf_idf_vector = tfidf_transformer.transform(count_vectorizer.transform([doc])) # 문서의 tf-idf 추출
sorted_keywords = sort_keywords(tf_idf_vector.tocoo()) # TF-IDF를 기준으로 역순 정렬

# 사용자가 지정한 갯수만큼 키워드 추출
keywords = extract_keywords(feature_names, sorted_keywords, 5)

print("\n===== 원문 =====")
print(docs[0][:100])
print("\n=== 핵심키워드 ===")
for k in keywords:
    print(k)


===== 원문 =====
과기정통부, 22일 유영민 장관 등 참석해 기념행사2021년까지 1516억원 투입, 5100여종 데이터 구축민간 클라우드 통한 외부연계체계도.."개방성 강화"[이데일리 이재운 기자

=== 핵심키워드 ===
('플랫', 0.2508899676053591)
('계획', 0.21504854366173637)
('정통부', 0.17920711971811365)
('데일리', 0.17920711971811365)
('과기', 0.17920711971811365)


In [11]:
tf_idf_vector.tocoo().data

array([0.03584142, 0.03584142, 0.03584142, 0.03584142, 0.05783327,
       0.07168285, 0.03584142, 0.03584142, 0.03584142, 0.02891664,
       0.03584142, 0.14458318, 0.03584142, 0.03584142, 0.02891664,
       0.02891664, 0.07168285, 0.11566654, 0.03584142, 0.03584142,
       0.04800684, 0.03584142, 0.03584142, 0.25088997, 0.03584142,
       0.02891664, 0.03584142, 0.02891664, 0.02891664, 0.03584142,
       0.03584142, 0.10752427, 0.17349981, 0.07168285, 0.03584142,
       0.10752427, 0.03584142, 0.07168285, 0.03584142, 0.03584142,
       0.02891664, 0.02891664, 0.07168285, 0.03584142, 0.04038487,
       0.02400342, 0.07168285, 0.03584142, 0.03584142, 0.10752427,
       0.03584142, 0.03584142, 0.10752427, 0.03584142, 0.03584142,
       0.02891664, 0.03584142, 0.03584142, 0.02400342, 0.03584142,
       0.02891664, 0.03584142, 0.03584142, 0.03584142, 0.10752427,
       0.02891664, 0.03584142, 0.02891664, 0.03584142, 0.1200171 ,
       0.07168285, 0.17920712, 0.02891664, 0.04038487, 0.02891


---


## 실습 2. gensim 활용


### 1) 전처리

In [12]:
from konlpy.tag import Mecab
mecab = Mecab()

preprocessed_docs = []
for doc in docs :
    # 명사와 동사만으로 문서 전처리
    preprocessed_docs.append(' '.join([token[0] for token in mecab.pos(doc) if token[1][0] in ['N', 'V']]))
preprocessed_docs[0][:100]

'과기 정통부 일 유영민 장관 등 참석 기념행사 년 억 원 투입 여종 데이터 구축 민간 클라우드 통한 외부 연계 체계 개방 강화 데일리 이재운 기자 국가 차원 빅 데이터 활용 시대 '

### 2) TF-IDF 계산

In [13]:
from gensim.models import TfidfModel
from gensim.corpora import Dictionary

document_ls = [doc.split() for doc in preprocessed_docs]
dct = Dictionary(document_ls) # 인덱스(key) - 단어(value) 인 딕셔너리 생성
corpus = [dct.doc2bow(doc) for doc in document_ls] # 각 문서에 포함된 단어를 인덱스로 변환하여 corpus 생성
tfidf = TfidfModel(corpus) # TF-IDF 산출

### 3) 핵심키워드 추출

In [14]:
def sort_keywords(tfidf):
    return sorted(tfidf, key=lambda x: (x[1], x[0]), reverse=True)

def extract_keywords(feature_names, sorted_keywords, n=5):
    return [(feature_names[idx], score) for idx, score in sorted_keywords[:n]]

In [15]:
doc = corpus[0]

sorted_keywords = sort_keywords(tfidf[doc]) # TF-IDF를 기준으로 역순 정렬

# 사용자가 지정한 갯수만큼 키워드 추출
keywords = extract_keywords(dct, sorted_keywords, 5)

print("\n=== 핵심키워드 ===")
for k in keywords:
    print(k)


=== 핵심키워드 ===
('플랫', 0.25708103651841274)
('폼', 0.25708103651841274)
('계획', 0.2203551741586395)
('정통부', 0.18362931179886624)
('데일리', 0.18362931179886624)


In [16]:
tfidf[doc]

[(0, 0.03672586235977325),
 (1, 0.020908894366388927),
 (2, 0.0734517247195465),
 (3, 0.0734517247195465),
 (6, 0.03672586235977325),
 (7, 0.010183852746009204),
 (8, 0.020908894366388927),
 (9, 0.03672586235977325),
 (10, 0.03672586235977325),
 (11, 0.03672586235977325),
 (13, 0.06272668309916678),
 (15, 0.03672586235977325),
 (16, 0.041817788732777854),
 (17, 0.020908894366388927),
 (18, 0.03672586235977325),
 (19, 0.020908894366388927),
 (20, 0.03672586235977325),
 (21, 0.005091926373004602),
 (22, 0.03672586235977325),
 (23, 0.020908894366388927),
 (24, 0.005091926373004602),
 (25, 0.0734517247195465),
 (26, 0.02545963186502301),
 (27, 0.03672586235977325),
 (28, 0.2203551741586395),
 (29, 0.03672586235977325),
 (30, 0.010183852746009204),
 (31, 0.03672586235977325),
 (32, 0.0734517247195465),
 (33, 0.03672586235977325),
 (34, 0.011656561215152345),
 (35, 0.03672586235977325),
 (36, 0.18362931179886624),
 (37, 0.041817788732777854),
 (38, 0.03672586235977325),
 (39, 0.0418177887327



---



# 1.2 Textrank
https://web.eecs.umich.edu/~mihalcea/papers/mihalcea.emnlp04.pdf

<img src="https://3.bp.blogspot.com/-yp0Lr3ec5EY/XIs6znCcO_I/AAAAAAAAAPY/xtZxe_OYtH0xeuWsp4Qd4DQrunGMpVQmQCLcBGAs/s640/keyword-extraction-textrank.png" />

## 실습 1. 행렬 활용


In [17]:
doc = '딸기 바나나 사과 딸기 파인애플'

### 1) 토큰화 (Tokenization)

분석 텍스트 정제

In [18]:
tokens = doc.split()
tokens

['딸기', '바나나', '사과', '딸기', '파인애플']

### 2) Unique한 토큰 목록 생성

그래프 생성을 위해서 Unique한 토큰 목록 생성

In [19]:
1 in [1, 3, 5]

True

In [20]:
# set(tokens)

unique_tokens = [] # 유니크한 토큰 목록을 담을 변수
for token in tokens: # 토큰들 하나씩 꺼내보기
    # print(token)
    # 있는지 없는지 체크
    have_token = token in unique_tokens # boolean
    if have_token:
        # 추가하지 않는다.
        pass
    else: # 없으면
        # 추가한다
        unique_tokens.append(token)

unique_tokens

['딸기', '바나나', '사과', '파인애플']

In [21]:
nodes = unique_tokens
nodes

['딸기', '바나나', '사과', '파인애플']

In [22]:
node2idx = {node: i for i, node in enumerate(nodes)}
node2idx

{'딸기': 0, '바나나': 1, '사과': 2, '파인애플': 3}

In [23]:
node_scores = [1.0] * len(nodes)
node_scores

[1.0, 1.0, 1.0, 1.0]

In [24]:
node_scores[ node2idx['딸기'] ]

1.0

In [25]:
tokens

['딸기', '바나나', '사과', '딸기', '파인애플']

In [26]:
temp = ('123', '234') # immutable 바꿀수 없는 str, int, float
# mutable set, dict, list
temp[0] = '777'

TypeError: 'tuple' object does not support item assignment

In [27]:
# 엣지(연결 선) 정보 - 리스트
window_size = 2
edges = []

for window_start in range(len(tokens) - 1):
    # context
    start_token = tokens[window_start]
    end_token = tokens[window_start + 1]

    edges.append( (start_token, end_token) )
    edges.append( (end_token, start_token) )

unique_edges = list(set(edges))
unique_edges

[('바나나', '딸기'),
 ('사과', '바나나'),
 ('사과', '딸기'),
 ('딸기', '바나나'),
 ('딸기', '사과'),
 ('딸기', '파인애플'),
 ('파인애플', '딸기'),
 ('바나나', '사과')]

In [28]:
print(tokens)
print(nodes)

['딸기', '바나나', '사과', '딸기', '파인애플']
['딸기', '바나나', '사과', '파인애플']


In [29]:
for node in nodes:
    print(node)

딸기
바나나
사과
파인애플


In [30]:
edges = {node: set() for node in nodes}
edges

{'딸기': set(), '바나나': set(), '사과': set(), '파인애플': set()}

In [31]:
tokens

['딸기', '바나나', '사과', '딸기', '파인애플']

In [32]:
# 엣지(연결 선) 정보 - 딕셔너리
window_size = 2
edges = { node: set() for node in nodes }

for window_start in range(len(tokens) - 1):
    # context
    start_token = tokens[window_start]
    end_token = tokens[window_start + 1]

    edges[start_token].add(end_token) # set().add()
    edges[end_token].add(start_token)

edges

{'딸기': {'바나나', '사과', '파인애플'},
 '바나나': {'딸기', '사과'},
 '사과': {'딸기', '바나나'},
 '파인애플': {'딸기'}}

In [33]:
nodes, node_scores, edges

(['딸기', '바나나', '사과', '파인애플'],
 [1.0, 1.0, 1.0, 1.0],
 {'딸기': {'바나나', '사과', '파인애플'},
  '바나나': {'딸기', '사과'},
  '사과': {'딸기', '바나나'},
  '파인애플': {'딸기'}})

In [34]:
node_scores

[1.0, 1.0, 1.0, 1.0]

In [35]:
d = 0.85
def cal_score():
    new_scores = [0] * len(nodes)
    for target_node in nodes:
        edge_weight_sum = 0
        # 나에게 들어오는 노드들
        for in_node in edges[target_node]:
            # 몇개 노드와 연결?
            out_vj = len(edges[in_node])
            # 현재 스코어는?
            S_vj = node_scores[ node2idx[in_node] ]
            edge_weight = S_vj/out_vj

            edge_weight_sum += edge_weight

        S_vi = (1-d) + d * edge_weight_sum
        # print(S_vi)
        # new_scores.append(S_vi)
        new_scores[node2idx[target_node]] = S_vi
    return new_scores

node_scores = cal_score()
node_scores

[1.85, 0.8583333333333333, 0.8583333333333333, 0.43333333333333335]

In [36]:
nodes

['딸기', '바나나', '사과', '파인애플']

In [37]:
edges

{'딸기': {'바나나', '사과', '파인애플'},
 '바나나': {'딸기', '사과'},
 '사과': {'딸기', '바나나'},
 '파인애플': {'딸기'}}

In [38]:
for target_node in nodes:
    print(edges[target_node])

{'파인애플', '바나나', '사과'}
{'딸기', '사과'}
{'딸기', '바나나'}
{'딸기'}


In [39]:
for target_node in nodes:
    for in_node in edges[target_node]:
        print(in_node)

파인애플
바나나
사과
딸기
사과
딸기
바나나
딸기


In [40]:
for target_node in nodes:
    for in_node in edges[target_node]:
        print(edges[in_node])

{'딸기'}
{'딸기', '사과'}
{'딸기', '바나나'}
{'파인애플', '바나나', '사과'}
{'딸기', '바나나'}
{'파인애플', '바나나', '사과'}
{'딸기', '사과'}
{'파인애플', '바나나', '사과'}


In [41]:
for epoch in range(30):
    node_scores = cal_score()
node_scores

[1.4669436757214278,
 0.9837112181478378,
 0.9837112181478378,
 0.5656338879828968]

In [42]:
for epoch in range(30):
    node_scores = cal_score()

node_scores

[1.4669434685405216,
 0.9837112743532095,
 0.9837112743532095,
 0.5656339827530596]

In [43]:
# 특정 노드의 Textrank 점수 = (1-d) + d * (나한테 들어오는 엣지 가중치들의 합)


### 3) 그래프 생성 (weighted edge 계산)

*   TextRank는 그래프 기반 모델
*   각 단어(토큰)은 그래프의 노드(vertex)
*   weighted_edge 행렬은 노드간 가중치 정보를 담고 있음
*   weighted_edge[i][j] 는 i번째 단어와 j번째 단어의 가중치를 의미
*   weighted_edge[i][j] 가 0인 경우는 노드간 연결이 없음을 의미
*   모든 노드는 1로 초기화

In [44]:
# 그래프 구조 잡기

# 무방향
    # 시작노드에 끝 노드 추가
    # 끝 노드에도 시작 노드 추가

# 1. window_size 만큼 토큰들을 가져온다 (context)
# 2. 2개씩 짝지어준다 (조합) -> 이중 반복문
# 3. edges에 추가해준다 (중복 x) set 자료형 활용


### 4) 각 노드의 score계산
각 노드와 연결된 weighted edge의 값을 합산

In [45]:
# score 계산 로직

# 1. Textrank score 계산할 노드 선택 (반복문)
# 2. 해당 노드와 연결된 노드들 (반복문)
    # score, 연결된 노드 수를 통해 엣지 가중치 계산
    # 새로운 score를 new_scores에 담아준다
# 3. 계산이 끝나면 기존 노드 스코어 갱신


### 5) 핵심 단어 추출

In [ ]:
import numpy as np
np.argsort(node_scores)[::-1]
idx2node

### 행렬 자료구조 활용

edges만 변경됨

In [47]:
edges = [[0] * len(nodes) for _ in nodes]
print(*edges, sep='\n')

[0, 0, 0, 0]
[0, 0, 0, 0]
[0, 0, 0, 0]
[0, 0, 0, 0]


In [48]:
# edges[start_node][end_node] => 연결된 상태 확인 가능
for window_start in range(len(tokens) - 1):
    start_node = tokens[window_start]
    end_node = tokens[window_start+1]
    # print(start_node, end_node)
    edges[node2idx[start_node]][node2idx[end_node]] = 1 # 연결 됨
    edges[node2idx[end_node]][node2idx[start_node]] = 1 # 연결 됨

print(*edges, sep='\n')

[0, 1, 1, 1]
[1, 0, 1, 0]
[1, 1, 0, 0]
[1, 0, 0, 0]


In [49]:
weight_edge_matrix = edges.copy()
weight_edge_matrix

[[0, 1, 1, 1], [1, 0, 1, 0], [1, 1, 0, 0], [1, 0, 0, 0]]

In [50]:
from copy import deepcopy
weight_edge_matrix = deepcopy(edges)

In [51]:
weight_edge_matrix[0][1] = 0
edges

[[0, 1, 1, 1], [1, 0, 1, 0], [1, 1, 0, 0], [1, 0, 0, 0]]

In [52]:
weight_edge_matrix

[[0, 0, 1, 1], [1, 0, 1, 0], [1, 1, 0, 0], [1, 0, 0, 0]]

In [53]:
node_scores = [1.0] * len(nodes)
weight_edge_matrix = deepcopy(edges)

for start_node in nodes:
    start_idx = node2idx[start_node]
    out_vi = sum(edges[start_idx])
    for end_node in nodes:
        end_idx = node2idx[end_node]
        weight_edge_matrix[start_idx][end_idx] = edges[start_idx][end_idx] * node_scores[start_idx] / out_vi # 엣지 가중치 = 스코어 / 내가 연결된 개수
#
weight_edge_matrix

[[0.0, 0.3333333333333333, 0.3333333333333333, 0.3333333333333333],
 [0.5, 0.0, 0.5, 0.0],
 [0.5, 0.5, 0.0, 0.0],
 [1.0, 0.0, 0.0, 0.0]]

In [54]:
new_scores = []
for node in nodes:
    node_idx = node2idx[node]
    weight_edge_sum = 0
    for row in weight_edge_matrix:
        weight_edge_sum += row[node_idx]
    new_scores.append((1-d)+d*weight_edge_sum)

new_scores

[1.85, 0.8583333333333333, 0.8583333333333333, 0.43333333333333335]

### numpy array

In [55]:
nodes, node_scores, edges

node_scores = np.array(node_scores)
edges = np.array(edges)

In [56]:
edges

array([[0, 1, 1, 1],
       [1, 0, 1, 0],
       [1, 1, 0, 0],
       [1, 0, 0, 0]])

In [57]:
edges.sum(axis=0)

array([3, 2, 2, 1])

In [58]:
weight_edge_matrix = edges * node_scores.reshape(-1, 1) / edges.sum(axis=0).reshape(-1, 1)
weight_edge_matrix

array([[0.        , 0.33333333, 0.33333333, 0.33333333],
       [0.5       , 0.        , 0.5       , 0.        ],
       [0.5       , 0.5       , 0.        , 0.        ],
       [1.        , 0.        , 0.        , 0.        ]])

In [59]:
new_scores = 1 - d + d*weight_edge_matrix.sum(axis=0)

In [60]:
new_scores

array([1.85      , 0.85833333, 0.85833333, 0.43333333])

In [61]:
for epoch in range(30):
    weight_edge_matrix = edges * node_scores.reshape(-1, 1) / edges.sum(axis=0).reshape(-1, 1)
    new_scores = 1 - d + d * weight_edge_matrix.sum(axis=0)
    node_scores = new_scores

node_scores

array([1.46694313, 0.98371137, 0.98371137, 0.56563414])

---

## 실습 2. 그래프 활용

In [62]:
import requests
from bs4 import BeautifulSoup

def get_news_by_url(url):
    res = requests.get(url, headers = {
        'User-Agent': 'Mozilla/5.0'
    })
    bs = BeautifulSoup(res.content, 'html.parser')

    title = bs.select_one('#title_area').text #제목
    content = bs.select_one('#contents').get_text().replace('\n', " ") #본문
    content = content.replace("// flash 오류를 우회하기 위한 함수 추가 function _flash_removeCallback() {}", "")
    return content.strip()

doc = get_news_by_url('https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=105&oid=018&aid=0004430108')
doc[:50]

'과기정통부, 22일 유영민 장관 등 참석해 기념행사2021년까지 1516억원 투입, 510'

### 1) 토큰화 (Tokenization)

분석 텍스트 정제

In [63]:
from konlpy.tag import Mecab
mecab = Mecab()

nodes = [token for token in mecab.pos(doc) if token[1] in ['NNG','NNP']] #NNG, NNP를 스코어 계산 대상(노드)로 제한
tokens = [token for token in mecab.pos(doc)] #탐색할 토큰 전체

### 2) 그래프 생성 (weighted edge 계산)

*   TextRank는 그래프 기반 모델
*   각 단어(토큰)은 그래프의 노드(vertex) 없음을 의미
*   모든 노드는 1로 초기화

In [64]:
%pip install networkx

Note: you may need to restart the kernel to use updated packages.


In [65]:
import numpy as np
import math
import networkx as nx

# 윈도내 동시 등장한 토큰으로 그래프를 생성
def connect(nodes, tokens) :
    window_size = 2 # coocurrence를 판단하기 위한 window 사이즈 설정

    edges = []
    for window_start in range(0,(len(tokens)-window_size+1)):
        window = tokens[window_start:window_start+window_size]
        for i in range(window_size) :
            for j in range(i+1, window_size) :
                if (window[i] in nodes) & (window[j] in nodes) : #윈도 내 단어가 노드에 속하는 경우만 엣지로 연결
                    edges.append((window[i], window[j]))
                    print((window[i], window[j]))
    return edges

# tokens = ['딸기', '바나나', '사과', '딸기', '파인애플']
# nodes = ['바나나', '사과', '파인애플', '딸기']

graph=nx.diamond_graph()
graph.clear()
graph.add_nodes_from(list(set(nodes))) #node 등록
graph.add_edges_from(connect(nodes, tokens)) #edge 연결

(('과기', 'NNG'), ('정통부', 'NNG'))
(('유영민', 'NNP'), ('장관', 'NNG'))
(('여종', 'NNG'), ('데이터', 'NNG'))
(('데이터', 'NNG'), ('구축', 'NNG'))
(('구축', 'NNG'), ('민간', 'NNG'))
(('민간', 'NNG'), ('클라우드', 'NNP'))
(('외부', 'NNG'), ('연계', 'NNG'))
(('연계', 'NNG'), ('체계', 'NNG'))
(('데일리', 'NNP'), ('이재운', 'NNP'))
(('이재운', 'NNP'), ('기자', 'NNG'))
(('국가', 'NNG'), ('차원', 'NNG'))
(('빅', 'NNG'), ('데이터', 'NNG'))
(('데이터', 'NNG'), ('활용', 'NNG'))
(('활용', 'NNG'), ('시대', 'NNG'))
(('산업', 'NNG'), ('창출', 'NNG'))
(('기존', 'NNG'), ('산업', 'NNG'))
(('데이터', 'NNG'), ('경제', 'NNG'))
(('과학', 'NNG'), ('기술', 'NNG'))
(('기술', 'NNG'), ('정보', 'NNG'))
(('정보', 'NNG'), ('통신부', 'NNG'))
(('서울', 'NNP'), ('중구', 'NNP'))
(('중구', 'NNP'), ('대한', 'NNP'))
(('대한', 'NNP'), ('상공', 'NNG'))
(('상공', 'NNG'), ('회의소', 'NNG'))
(('데이터', 'NNG'), ('생태', 'NNG'))
(('기반', 'NNG'), ('마련', 'NNG'))
(('빅', 'NNG'), ('데이터', 'NNG'))
(('데이터', 'NNG'), ('플랫', 'NNG'))
(('플랫', 'NNG'), ('폼', 'NNG'))
(('출범식', 'NNG'), ('행사', 'NNG'))
(('유영민', 'NNP'), ('과기', 'NNG'))
(('과기', 'NNG'), ('정통부',

### 3) 스코어 계산 및 핵심키워드 추출

In [66]:
scores = nx.pagerank(graph) #pagerank 계산
rank = sorted(scores.items(), key=lambda x: x[1], reverse=True) #score 역순 정렬
print("\n=== 핵심키워드 ===")
rank[:5]


=== 핵심키워드 ===


[(('데이터', 'NNG'), 0.03721496487820151),
 (('정보', 'NNG'), 0.014138071058410556),
 (('활용', 'NNG'), 0.012760755336874941),
 (('기사', 'NNG'), 0.011742499548955487),
 (('언론사', 'NNG'), 0.01163519268572504)]

In [67]:
import networkx as nx
from IPython.core.display import Image
from networkx.drawing.nx_pydot import to_pydot

d = to_pydot(graph)
d.set_dpi(600)
d.set_rankdir("LR")
Image(d.create_png(), width=600)

---

## 실습 3. TextRank 핵심 구 추출

### 1) 불용어를 기준으로 구 추출

In [68]:
phrases = []
phrase = ' '

for word in tokens:
    if word[1][0] != 'N':
        if phrase != ' ':
            phrases.append(phrase.strip())
        phrase= ' '
    else:
        phrase+=word[0]
        phrase+= ' '

print(phrases)

['과기 정통부', '일 유영민 장관 등 참석', '기념행사', '년', '억 원 투입', '여종 데이터 구축 민간 클라우드', '외부 연계 체계', '개방', '강화', '데일리 이재운 기자', '국가 차원', '빅 데이터 활용 시대', '산업 창출', '기존 산업', '변화', '혁신', '장', '센터', '문', '개 분야', '데이터 경제', '발전', '정부', '청사진', '현실', '구현', '데', '계획', '일 과학 기술 정보 통신부', '서울 중구 대한 상공 회의소', '데이터 생태', '조성', '혁신', '장', '기반 마련', '빅 데이터 플랫 폼', '센터', '출범식 행사', '개최', '유영민 과기 정통부 장관', '노웅래 국회 과학 기술 정보 방송 통신 위원회 위원장 등', '명', '참가', '개 분야', '개 센터', '년 간', '억 원 투입 이미지', '픽사 베이 빅 데이터', '데이터 활용', '혁신', '장', '문재', '정부', '경제 성장 핵심 요소 중 하나', '문재인 대통령', '데이터 활용', '이', '정보 보호', '보안', '중요', '강조', '맥락 속', '빅 데이터 센터', '공공', '민간', '협업', '활용', '양질', '데이터', '생산', '구축', '플랫 폼', '이', '수집', '분석', '유통', '역할', '담당', '과기 정통부', '분야', '플랫 폼', '개소', '이', '연계', '기관', '센터', '개소', '구축', '데', '년', '억 원', '투입', '계획', '올해', '억 원 규모', '사업', '추진', '대상 분야', '금융', '카드', '환경', '한국 수자원 공사', '문화', '한국 문화 정보원', '교통', '한국 교통 연구원', '헬 스케어', '국립암센터', '유통', '소비', '매일 방송', '통신', '중소기업', '비즈', '지역 경제', '경기도 청', '산림', '한국 임업', '흥원', '등', '차 공모', '개 빅 데이

In [69]:
unique_phrases = []

for phrase in phrases:
    if phrase not in unique_phrases:
        unique_phrases.append(phrase)

print(unique_phrases)

['과기 정통부', '일 유영민 장관 등 참석', '기념행사', '년', '억 원 투입', '여종 데이터 구축 민간 클라우드', '외부 연계 체계', '개방', '강화', '데일리 이재운 기자', '국가 차원', '빅 데이터 활용 시대', '산업 창출', '기존 산업', '변화', '혁신', '장', '센터', '문', '개 분야', '데이터 경제', '발전', '정부', '청사진', '현실', '구현', '데', '계획', '일 과학 기술 정보 통신부', '서울 중구 대한 상공 회의소', '데이터 생태', '조성', '기반 마련', '빅 데이터 플랫 폼', '출범식 행사', '개최', '유영민 과기 정통부 장관', '노웅래 국회 과학 기술 정보 방송 통신 위원회 위원장 등', '명', '참가', '개 센터', '년 간', '억 원 투입 이미지', '픽사 베이 빅 데이터', '데이터 활용', '문재', '경제 성장 핵심 요소 중 하나', '문재인 대통령', '이', '정보 보호', '보안', '중요', '강조', '맥락 속', '빅 데이터 센터', '공공', '민간', '협업', '활용', '양질', '데이터', '생산', '구축', '플랫 폼', '수집', '분석', '유통', '역할', '담당', '분야', '개소', '연계', '기관', '억 원', '투입', '올해', '억 원 규모', '사업', '추진', '대상 분야', '금융', '카드', '환경', '한국 수자원 공사', '문화', '한국 문화 정보원', '교통', '한국 교통 연구원', '헬 스케어', '국립암센터', '소비', '매일 방송', '통신', '중소기업', '비즈', '지역 경제', '경기도 청', '산림', '한국 임업', '흥원', '등', '차 공모', '개 빅 데이터 센터', '선정', '다음 달', '일', '개', '추가 선정', '지원', '운영', '데이터 생태계', '기업', '경쟁력', '제고', '수행', '주요 활용 전략', '사례', '빅 데이터 활용', '신

### 2) 각 구의 Score 계산

앞서 산출한 각 단어별 점수를 합산

In [70]:
vocabs = dict((r[0][0], r[1]) for r in rank)
phrase_scores = []
keywords = []

for phrase in unique_phrases:
    phrase_score = 0
    for word in phrase.split():
        if word in vocabs.keys():
            phrase_score+=vocabs[word]

    phrase_scores.append((phrase, phrase_score))

for phrase_score in phrase_scores[:10]:
    print(f"keyword: {phrase_score[0]}, Score : {phrase_score[1]}")

keyword: 과기 정통부, Score : 0.011153534220667082
keyword: 일 유영민 장관 등 참석, Score : 0.009812231472621002
keyword: 기념행사, Score : 0.0007144558228149565
keyword: 년, Score : 0
keyword: 억 원 투입, Score : 0.004763038818766374
keyword: 여종 데이터 구축 민간 클라우드, Score : 0.056664453727209456
keyword: 외부 연계 체계, Score : 0.014289116456299121
keyword: 개방, Score : 0.0007144558228149565
keyword: 강화, Score : 0.0007144558228149565
keyword: 데일리 이재운 기자, Score : 0.012470446359718267


### 3) 각 구를 Score로 정렬하여 핵심 구 추출

In [71]:
sorted_phrase_score = sorted(phrase_scores, key=lambda tup: tup[1], reverse=True)
sorted_phrase_score[:10]

[('여종 데이터 구축 민간 클라우드', 0.056664453727209456),
 ('민간 사이 데이터 파일 형식 등', 0.05525218283665386),
 ('빅 데이터 활용 시대', 0.054877458807888066),
 ('빅 데이터 플랫 폼', 0.052490554069070286),
 ('빅 데이터 활용', 0.052355436793158024),
 ('노웅래 국회 과학 기술 정보 방송 통신 위원회 위원장 등', 0.05176587443591581),
 ('데이터 활용', 0.04997572021507645),
 ('여종 신규 데이터', 0.04965988966721664),
 ('여종 데이터 구축', 0.04767044771826788),
 ('픽사 베이 빅 데이터', 0.047565711789215016)]



---



## 실습 4. gensim 활용

- summarization.keywords(document, words) : document를 요약하여 words만큼 키워드를 추출

In [72]:
%pip install gensim==3.6.0

Note: you may need to restart the kernel to use updated packages.


In [73]:
preprocessed_docs[0]

'과기 정통부 일 유영민 장관 등 참석 기념행사 년 억 원 투입 여종 데이터 구축 민간 클라우드 통한 외부 연계 체계 개방 강화 데일리 이재운 기자 국가 차원 빅 데이터 활용 시대 열린다 새로운 산업 창출 기존 산업 변화 이르 혁신 장 위한 센터 문 연다 개 분야 걸쳐 데이터 경제 발전 위한 정부 청사진 현실 구현 데 앞장선다는 계획 이 일 과학 기술 정보 통신부 서울 중구 대한 상공 회의소 데이터 생태 조성 혁신 장 기반 마련 위한 빅 데이터 플랫 폼 센터 출범식 행사 개최 유영민 과기 정통부 장관 노웅래 국회 과학 기술 정보 방송 통신 위원회 위원장 등 명 참가 개 분야 개 센터 년 간 억 원 투입 이미지 픽사 베이 빅 데이터 데이터 활용 통해 혁신 장 이루 문재 인 정부 경제 성장 핵심 요소 중 하나 다 문재인 대통령 올 들 데이터 활용 이 따른 정보 보호 보안 대한 중요 강조 했 맥락 속 빅 데이터 센터 공공 민간 협업 활용 높 양질 데이터 생산 구축 플랫 폼 이 수집 분석 유통 역할 담당 과기 정통부 분야 플랫 폼 개소 이 연계 기관 센터 개소 구축 데 년 억 원 투입 계획 이 올해 억 원 규모 사업 추진 있 대상 분야 금융 카드 환경 한국 수자원 공사 문화 한국 문화 정보원 교통 한국 교통 연구원 헬 스케어 국립암센터 유통 소비 매일 방송 통신 중소기업 존 비즈 온 지역 경제 경기도 청 산림 한국 임업 흥원 등 차 공모 통해 개 빅 데이터 센터 선정 다음 달 일 차 공모 통해 개 추가 선정 개 지원 운영 계획 이 이 통해 데이터 생태계 혁신 기업 경쟁력 제고 역할 수행 주요 활용 전략 사례 보 빅 데이터 활용 통해 신 新 시장 창출 방안 담 있 금융 플랫 폼 경우 소 상공 인 신용 평가 고도 등 통해 금융 취약 계층 대상 중 금리 대출 자를 절감 연간 조 원 신규 대출 창출 전망 이 유통 소비 중소기업 플랫 폼 소상 공인 중소기업 폐업 감소 문화 플랫 폼 문화 예술 관람 생활 체육 참여 높이 방안 모색 의료비 절감 헬스 케어 기업 매출 향상 통한 산

In [74]:
from gensim.summarization import keywords
keywords(preprocessed_docs[0], words=5).split('\n')

['데이터', '데일리 이재운', '언론사', '지렛대']